# Moving averages in Python

In [ ]:
from pandas import DataFrame
import matplotlib.pyplot as plt
from data201 import db_connection

%matplotlib inline

In [ ]:
conn = db_connection(config_file='stock-prices.ini')
cursor = conn.cursor()

In [ ]:
table = cursor.execute('SELECT * FROM recent_prices')
table = cursor.fetchall()
table

In [ ]:
def compute_moving_averages(table, n):
    """
    @table the table of days, prices, and averages
    @n the number of prices to average
    """
    last_prices = []  # last n prices

    for i in range(len(table)):
        last_prices += [table[i][1],]  # append a new price
        
        if i >= n:
            last_prices.pop(0)   # remove the oldest price
            
        if i < n - 1:
            table[i] += (None,)  # no average for first n-1 days
        else:
            table[i] += (sum(last_prices)/n,)  # moving average

    return table

In [ ]:
for days in [3, 5, 10]:
    table = compute_moving_averages(table, days)
    
table

In [ ]:
columns = ['days ago', 'price']

for days in [3, 5, 10]:
    label = f'{days}_day_moving_average'
    columns += [label,]

df = DataFrame(table)
df.columns = columns
df

In [ ]:
rows = df.values.tolist()
xs   = [row[0] for row in rows]
ys   = [row[1] for row in rows]

plt.figure(figsize=(15, 10))

# Initialize the graph and plot the prices.
plt.xticks(xs)
plt.plot(xs, ys, linewidth=5)
plt.title('Moving Average of Stock Prices')
plt.xlabel('Days ago')
plt.ylabel('Price')

days_ago = [3, 5, 10]

for i in range(len(days_ago)):
    days = days_ago[i]
    graph_label = f'{days}_day_moving_average'

    xs   = [row[0] for row in rows]
    ys   = [row[1] for row in rows]
    avgs = [row[i + 2] for row in rows]
    
    # Plot the moving average line.
    plt.plot(xs[days - 1:], avgs[days - 1:], label=graph_label)
    
plt.legend()
plt.show()

In [ ]:
cursor.close()
conn.close()